# PC Lab 4

In [1]:
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
from sklearn.model_selection import ParameterGrid
from sklearn.preprocessing import MinMaxScaler, StandardScaler
from sklearn.metrics import mean_squared_error, r2_score
from statsmodels.api import OLS
from sklearn.linear_model import Ridge, LinearRegression
from sklearn.ensemble import RandomForestRegressor
from xgboost import XGBRegressor
import keras
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense, Dropout, Input, Bidirectional, RNN, GRU
from tensorflow.keras.callbacks import EarlyStopping
from plotly.subplots import make_subplots
from tqdm.notebook import tqdm
from keras.optimizers import Adam

In [2]:
# setting a seed for reproducibility
keras.utils.set_random_seed(42)
tf.random.set_seed(42)

## Import Data

In [3]:
# load data
price_data = pd.read_csv('Data_PCLab4_Stock_Price.csv')
volume_data = pd.read_csv('Data_PCLab4_Stock_Volume.csv')   

In [4]:
# show head of price data
price_data.head()

Date       AAPL         BA          T    MGM        AMZN         IBM  \
0  2012-01-12  60.198570  75.510002  30.120001  12.13  175.929993  180.550003   
1  2012-01-13  59.972858  74.599998  30.070000  12.35  178.419998  179.160004   
2  2012-01-17  60.671429  75.239998  30.250000  12.25  181.660004  180.000000   
3  2012-01-18  61.301430  75.059998  30.330000  12.73  189.440002  181.070007   
4  2012-01-19  61.107143  75.559998  30.420000  12.80  194.449997  180.520004   

        TSLA        GOOG        sp500  
0  28.250000  313.644379  1295.500000  
1  22.790001  311.328064  1289.089966  
2  26.600000  313.116364  1293.670044  
3  26.809999  315.273285  1308.040039  
4  26.760000  318.590851  1314.500000

In [5]:
# show head of volume data
volume_data.head()

Date      AAPL       BA         T       MGM     AMZN      IBM  \
0  2012-01-12  53146800  3934500  26511100  17891100  5385800  6881000   
1  2012-01-13  56505400  4641100  22096800  16621800  4753500  5279200   
2  2012-01-17  60724300  3700100  23500200  15480800  5644500  6003400   
3  2012-01-18  69197800  4189500  22015000  18387600  7473500  4600600   
4  2012-01-19  65434600  5397300  25524000  14022900  7096000  8567200   

      TSLA      GOOG       sp500  
0   729300   3764400  4019890000  
1  5500400   4631800  3692370000  
2  4651600   3832800  4010490000  
3  1260200   5544000  4096160000  
4  1246300  12657800  4465890000

## Task 1

### Describe Data

In [6]:
volume_data.describe()

AAPL            BA             T           MGM          AMZN  \
count  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03   
mean   5.820332e+07  6.419916e+06  2.832131e+07  9.845582e+06  4.102673e+06   
std    4.568141e+07  9.711873e+06  1.428911e+07  7.295753e+06  2.290722e+06   
min    1.136200e+07  7.889000e+05  6.862400e+06  9.507000e+05  8.813000e+05   
25%    2.769930e+07  3.031850e+06  2.002150e+07  5.796450e+06  2.675700e+06   
50%    4.209420e+07  3.991000e+06  2.485930e+07  7.899800e+06  3.494800e+06   
75%    7.182480e+07  5.325900e+06  3.210565e+07  1.104055e+07  4.768150e+06   
max    3.765300e+08  1.032128e+08  1.950827e+08  9.009820e+07  2.385610e+07   

                IBM          TSLA          GOOG         sp500  
count  2.159000e+03  2.159000e+03  2.159000e+03  2.159000e+03  
mean   4.453090e+06  7.001302e+06  2.498238e+06  3.680732e+09  
std    2.462811e+06  5.781208e+06  1.928407e+06  8.622717e+08  
min    1.193000e+06  3.649000e+05  7.900000e+03  1.248960e+09  
25%    3.111250e+06  3.433450e+06  1.325400e+06  3.211890e+09  
50%    3.825000e+06  5.581100e+06  1.813900e+06  3.526890e+09  
75%    4.937300e+06  8.619550e+06  3.245350e+06  3.933290e+09  
max    3.049020e+07  6.093880e+07  2.497790e+07  9.044690e+09

In [7]:
# average trading volume for aapl:
aapl_avg_volume = volume_data['AAPL'].mean()
print('AAPL average trading volume: ', round(aapl_avg_volume, 2))
# max trading volume for S&P 500:
sp500_max_volume = volume_data['sp500'].max()
print('S&P 500 max trading volume: ', round(sp500_max_volume, 2))
# most traded stock:
total_volume = volume_data.iloc[:, 1:].sum()
most_traded = total_volume.drop('sp500').idxmax()
print('Most traded stock: ', most_traded)


AAPL average trading volume:  58203317.42
S&P 500 max trading volume:  9044690000
Most traded stock:  AAPL


### Plot Data

#### Volume

In [8]:
def plot_stock_vol(data, normalize=False):
    data = data.copy() # make a copy of the data
    for col in data.columns[1:]:
        if normalize:
            data[col] = (data[col] - data[col].mean()) / data[col].std() # normalize volume by S&P 500 volume
    title = 'Normalized stock volume' if normalize else 'Stock volume' # set title
    fig = px.line(data, x = 'Date', y = data.columns[:-1], title=title) # create plot
    fig.update_xaxes(title_text='Date') # set x-axis title
    fig.update_yaxes(title_text='Volume') # set y-axis title
    fig.update_layout(legend_title_text='Stock') # set legend title
    fig.show() # show plot
    if normalize == False:
        return print('Stock volume average:\n', pd.DataFrame({stock : round(data[stock].mean(), 2) for stock in data.columns[1:]}.items(), columns = ['Stock', 'Average Volume'])) # return average volume for each stock

plot_stock_vol(volume_data, normalize=False) # plot volume

Stock volume average:
    Stock  Average Volume
0   AAPL    5.820332e+07
1     BA    6.419916e+06
2      T    2.832131e+07
3    MGM    9.845582e+06
4   AMZN    4.102673e+06
5    IBM    4.453090e+06
6   TSLA    7.001302e+06
7   GOOG    2.498238e+06
8  sp500    3.680732e+09


Without normalization we can't make a truthful comparison of the stocks' volumes.

#### Normalized Volume

In [9]:
plot_stock_vol(volume_data, normalize=True) # plot volume

After normalizing, it appears that these stocks follow similar patterns, with occasional peaks in volumes. 

### Correlation

In [10]:
price_data['Date'] = pd.to_datetime(price_data['Date']) # convert date to datetime
volume_data['Date'] = pd.to_datetime(volume_data['Date']) # convert date to datetime
price_data.update(price_data.iloc[:, 1:].astype(float)) # convert prices to float
volume_data.update(volume_data.iloc[:, 1:].astype(float)) # convert volumes to float

In [11]:
return_data = price_data.drop('Date', axis = 1).copy() # make a copy of the price data
return_data = return_data.pct_change() # calculate daily returns
volume_change = volume_data.drop('Date', axis = 1).copy() # make a copy of the volume data
volume_change = volume_change.pct_change() # calculate daily volume changes
return_data = pd.concat([price_data['Date'], return_data], axis = 1) # add date to returns
volume_change = pd.concat([volume_data['Date'], volume_change], axis = 1) # add date to volume changes
return_data = return_data.iloc[1:, :]
volume_change = volume_change.iloc[1:, :]
corrs = {}
for stock in return_data.columns[1:]:
    df = pd.merge(return_data[['Date', stock]], volume_change[['Date', stock]], on='Date', suffixes = ['_return', '_volume_change']) # merge price and volume data    
    corrs[stock] = df.loc[:, [f'{stock}_return', f'{stock}_volume_change']].corr().iloc[0, 1] # store correlation in dictionary

In [12]:
fig = px.bar(x = list(corrs.keys()), y = list(corrs.values()), title='Correlation between stock returns and volume changes') # create plot
fig.update_xaxes(title_text='Stock') # set x-axis title
fig.update_yaxes(title_text='Correlation') # set y-axis title
fig.show() # show plot

In [13]:
corr_df = pd.DataFrame({'Avg Annual Return' : return_data.iloc[:, 1:].mean() * 252, 'Avg Volume Change' : volume_change.iloc[:, 1:].mean()}) # create dataframe with average return and volume change
corr_df = corr_df.sort_values(by='Avg Annual Return', ascending=False) # sort dataframe by average return
fig = px.bar(data_frame = corr_df, x = corr_df.index, y = 'Avg Annual Return', color = 'Avg Volume Change') # create plot
fig.update_xaxes(title_text='Stock') # set x-axis title
fig.update_yaxes(title_text='Average Annual Return') # set y-axis title
fig.update_layout(coloraxis_colorbar=dict(title='Average Volume Change')) # set colorbar title
fig.show() # show plot

The two plots represent respectively the correlation between the stock returns and the volume changes, and the average annual stock return compared to the average volume change. The main results we would like to highlight are:
- The correlation between stock return and volume changes is not consistent across stocks.
- There is not a clear pattern between high-low stock returns and high-low volume changes. Therefore, this particular interaction term cannot be considered significant in a potential factor model.

As a conclusion, data shows that the correlation is not significant.

## Task 2

### Group prices and volumes

In [14]:
# we concatenate date, stock price and volume data
concat_df_p = pd.concat([price_data['Date'], price_data.iloc[:, 1:], volume_data.iloc[:, 1:]], axis = 1)
concat_df_p.columns = ['Date'] + [f'{col}_price' for col in concat_df_p.columns[1:10]] + [f'{col}_volume' for col in concat_df_p.columns[10:]]
concat_df_p.head()

Date  AAPL_price   BA_price    T_price  MGM_price  AMZN_price  \
0 2012-01-12   60.198570  75.510002  30.120001      12.13  175.929993   
1 2012-01-13   59.972858  74.599998  30.070000      12.35  178.419998   
2 2012-01-17   60.671429  75.239998  30.250000      12.25  181.660004   
3 2012-01-18   61.301430  75.059998  30.330000      12.73  189.440002   
4 2012-01-19   61.107143  75.559998  30.420000      12.80  194.449997   

    IBM_price  TSLA_price  GOOG_price  sp500_price  AAPL_volume  BA_volume  \
0  180.550003   28.250000  313.644379  1295.500000     53146800    3934500   
1  179.160004   22.790001  311.328064  1289.089966     56505400    4641100   
2  180.000000   26.600000  313.116364  1293.670044     60724300    3700100   
3  181.070007   26.809999  315.273285  1308.040039     69197800    4189500   
4  180.520004   26.760000  318.590851  1314.500000     65434600    5397300   

   T_volume  MGM_volume  AMZN_volume  IBM_volume  TSLA_volume  GOOG_volume  \
0  26511100    17891100      5385800     6881000       729300      3764400   
1  22096800    16621800      4753500     5279200      5500400      4631800   
2  23500200    15480800      5644500     6003400      4651600      3832800   
3  22015000    18387600      7473500     4600600      1260200      5544000   
4  25524000    14022900      7096000     8567200      1246300     12657800   

   sp500_volume  
0    4019890000  
1    3692370000  
2    4010490000  
3    4096160000  
4    4465890000

### Scaling

In [15]:
stock_tickers = ['AAPL', 'BA', 'T', 'MGM', 'AMZN', 'IBM', 'TSLA', 'GOOG', 'sp500']

In [16]:
# we also create separate dataframes
aapl_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'AAPL_price' or col == 'AAPL_volume')]]
ba_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'BA_price' or col == 'BA_volume')]]
t_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'T_price' or col == 'T_volume')]]
mgm_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'MGM_price' or col == 'MGM_volume')]]
amzn_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'AMZN_price' or col == 'AMZN_volume')]]
ibm_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'IBM_price' or col == 'IBM_volume')]]
tsla_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'TSLA_price' or col == 'TSLA_volume')]]
goog_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'GOOG_price' or col == 'GOOG_volume')]]
sp500_df_price = concat_df_p.loc[:, ['Date'] + [col for col in concat_df_p.columns if (col == 'sp500_price' or col == 'sp500_volume')]]

# create a list with the names of the dataframes
price_dfs = [aapl_df_price, ba_df_price, t_df_price, mgm_df_price, amzn_df_price, ibm_df_price, tsla_df_price, goog_df_price, sp500_df_price]

for df in price_dfs:
    df.columns = ['Date', 'Price', 'Volume'] # rename columns

In [17]:
aapl_df_price.head()

Date      Price    Volume
0 2012-01-12  60.198570  53146800
1 2012-01-13  59.972858  56505400
2 2012-01-17  60.671429  60724300
3 2012-01-18  61.301430  69197800
4 2012-01-19  61.107143  65434600

We want to do the same thing for the returns, in order to have similar dataframes.

In [18]:
concat_df_r = pd.concat([price_data['Date'], return_data.iloc[:, 1:], volume_change.iloc[:, 1:]], axis = 1) # concatenate date, stock returns and volume changes
concat_df_r.columns = ['Date'] + [f'{col}_return' for col in concat_df_r.columns[1:10]] + [f'{col}_volume' for col in concat_df_r.columns[10:]]
concat_df_r.drop(0, inplace=True) # drop first row

# we also create separate dataframes
aapl_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'AAPL_return' or col == 'AAPL_volume')]]
ba_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'BA_return' or col == 'BA_volume')]]
t_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'T_return' or col == 'T_volume')]]
mgm_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'MGM_return' or col == 'MGM_volume')]]
amzn_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'AMZN_return' or col == 'AMZN_volume')]]
ibm_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'IBM_return' or col == 'IBM_volume')]]
tsla_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'TSLA_return' or col == 'TSLA_volume')]]
goog_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'GOOG_return' or col == 'GOOG_volume')]]
sp500_df_ret = concat_df_r.loc[:, ['Date'] + [col for col in concat_df_r.columns if (col == 'sp500_return' or col == 'sp500_volume')]]

# create a list with the names of the dataframes
return_dfs = [aapl_df_ret, ba_df_ret, t_df_ret, mgm_df_ret, amzn_df_ret, ibm_df_ret, tsla_df_ret, goog_df_ret, sp500_df_ret]

for df in return_dfs:
    df.columns = ['Date', 'Return', 'Volume'] # rename columns

In [19]:
aapl_df_ret.head()

Date    Return    Volume
1 2012-01-13 -0.003749  0.063195
2 2012-01-17  0.011648  0.074664
3 2012-01-18  0.010384  0.139541
4 2012-01-19 -0.003169 -0.054383
5 2012-01-20 -0.017417  0.581634

For each stock we now have two datframes, which display changes in returns and prices, respectively, against volumes.

### Price and Return prediction

<b>NOTE:</b> In the following section we will use as a benchmark the Apple stock, which will provide some initial insights on the performances of the different models. The metrics for all stocks combined will be further provided.

#### Prices - OLS

In [20]:
def roos_metric(y_test, test_preds, pred): #compute the roos metric
    if isinstance(test_preds, np.ndarray): # check if test_preds is a numpy array
        y_test = pd.Series(y_test)
        test_preds = pd.Series(test_preds)
    if pred == 'Price': # check if we are predicting price
        y_test = y_test.pct_change() # calculate price percentage change (return)
        test_preds = test_preds.pct_change() # calculate predicted price percentage change (return)
    return 1 - (np.sum(np.square(y_test - test_preds)) / np.sum(np.square(y_test))) 

def sign_concordance(y_test, test_preds, pred): # compute the sign concordance
    if pred == 'Price':
        y_test = y_test.pct_change()
        test_preds = test_preds.pct_change()
    return np.sum(np.sign(y_test) == np.sign(test_preds)) / len(y_test)

metric_dict = {'Roos' : roos_metric, 'Sign Concordance' : sign_concordance, 'MSE' : mean_squared_error, 'R2' : r2_score} #create a dictionary with the metrics

In [21]:
def ols_model(data, pred, market = None, test_size = 0.25, lags = 1, val_metric = ['Roos', 'MSE', 'R2', 'Sign Concordance'], plot=False, scaler = 'minmax'):
    data = data.copy() # make a copy of the data

    if market is not None: # check if market data is provided
        data[f'Market {pred}'] = market[pred] # add market data to the dataframe
    
    train_size = int(len(data) * (1 - test_size)) # calculate training size

    if isinstance(lags, list): # check if lags is a list
        data[f'Volume lag 1'] = data['Volume'].shift(1) # create lagged volume column
        if market is not None:
            data[f'Market {pred} Lag 1'] = data[f'Market {pred}'].shift(1) # create lagged market column
        for lag in lags: # iterate over lags if there are multiple lags
            data[f'{pred} Lag {lag}'] = data[pred].shift(lag) # create lagged price column
    else: #if laf is single value
        data[f'{pred} Lag {lags}'] = data[pred].shift(lags)
        data[f'Volume Lag {lags}'] = data['Volume'].shift(lags)
        if market is not None:
            data[f'Market {pred} Lag {lags}'] = data[f'Market {pred}'].shift(lags)
    
    data = data.dropna() # drop missing values

    X = data.drop(['Date', pred, 'Volume'], axis = 1) # training features
    y = pd.DataFrame(data[pred]) # training target
    if market is not None:
        X = X.drop([f'Market {pred}'], axis = 1)

    if scaler == 'minmax': #minmax scaling
        X_scaler = MinMaxScaler()
        y_scaler = MinMaxScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())
    
    elif scaler == 'standard': #standard scaling
        X_scaler = StandardScaler()
        y_scaler = StandardScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())

    y = pd.Series(y.values.flatten()) #flatten scaled output

    # train test split
    X_train, X_test = X[:train_size], X[train_size:] # split features into training and testing sets
    y_train, y_test = y[:train_size], y[train_size:] # split target into training and testing sets
    
    # model fitting
    model = LinearRegression() # create OLS model
    model.fit(X_train, y_train) # fit the model
    train_predictions = model.predict(X_train) # make predictions
    test_predictions = model.predict(X_test) # make predictions

    train_predictions_ret = pd.DataFrame(train_predictions) #create a dataframe with train predictions
    train_predictions_ret = pd.Series(y_scaler.inverse_transform(train_predictions_ret).flatten()) #inverse transform the predictions
    test_predictions_ret = pd.DataFrame(test_predictions) #create a dataframe with test predictions
    test_predictions_ret = pd.Series(y_scaler.inverse_transform(test_predictions_ret).flatten()) #inverse transform the predictions
    returns = np.hstack([train_predictions_ret, test_predictions_ret]) #stack the predictions

    if isinstance(val_metric, list): # in this section we save all the needed metrics in a dataframe
        metric = {}
        if scaler is not None:
            y_test_inv = pd.DataFrame(y_test)
            test_predictions_inv = pd.DataFrame(test_predictions)
            y_test_inv = pd.Series(y_scaler.inverse_transform(y_test_inv).flatten())
            test_predictions_inv = pd.Series(y_scaler.inverse_transform(test_predictions_inv).flatten())
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv, pred)
                else:
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv)
        else:
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test, test_predictions, pred)
                else:
                    metric[el] = metric_dict[el](y_test, test_predictions)
        metric = pd.DataFrame(metric.items(), columns = ['Metric', 'Value'])

    if plot: # plot the results
        fig = go.Figure()

        # Add the actual values line
        fig.add_trace(go.Scatter(x=data['Date'], y = y, mode='lines', name=f'Actual {pred}', line=dict(color='blue')))

        # Add the predicted values line
        fig.add_trace(go.Scatter(x=data['Date'], y=np.hstack([train_predictions, test_predictions]), mode='lines', name=f'Predicted {pred}', line=dict(color='red')))

        # Update the layout for titles and labels
        fig.update_layout(
            title=f'Predicted vs. Actual {pred}',
            xaxis_title='Date',
            yaxis_title=pred,
            legend_title="Legend",
            showlegend=True)

        # Show the plot
        fig.show()

    return model, metric, returns # return results and metric

In [22]:
# we fit the OLS model for AAPL stock price
model, metric, returns = ols_model(aapl_df_price, 'Price', plot=True)
print('The model performances are:\n', metric)

The model performances are:
              Metric      Value
0  Sign Concordance   0.478664
1               MSE  34.229125
2              Roos  -1.376238
3                R2   0.991505


At a first glance, the model seems to fit well the target price. Despite that, the Roos has a very negative value, suggesting that the out of sample performance is actually bad. More speficically, a negative Roos implies that the model is performing worse than simply predicting a return of 0 for t+1. The R2 is really high and the mse is reasonably low. However, if we zoom closely on the graph, it appeats that each predicted price is extremely similar to the previous day's price.

#### Returns - OLS

In [23]:
# fit a OLS model for AAPL stock return
model, metric, returns = ols_model(aapl_df_ret, 'Return', plot=True)
print('The model performances are:\n', metric)

The model performances are:
              Metric     Value
0  Sign Concordance  0.552876
1               MSE  0.000529
2              Roos -0.007691
3                R2 -0.014266


The graph seems to be showing poor predictive performances. As in the previous case, the Roos is negative, meaning that the model is close to predicting a return of 0 for the next period. It must be noted, however, that the sign concordance is high. 

These results for the OLS do not surprise us, since its purpose is that of minimizing the RSS. In the case of fluctuating returns and prices, this would imply that the regressor predicts returns that are very close to 0. This is also reflected in the MSE for returns predictions

#### Prices - Ridge

In [24]:
def ridge_model(data, pred, market = None, test_size = 0.25, lags = 1, val_metric = ['Roos', 'MSE', 'R2', 'Sign Concordance'], plot=False, scaler = 'minmax', penalty = 1.0):
   
    '''we apply the same strategy as in the OLS model, but we use a Ridge model'''
    
    data = data.copy() # make a copy of the data

    if market is not None:
        data[f'Market {pred}'] = market[pred]
    
    train_size = int(len(data) * (1 - test_size)) # calculate training size

    if isinstance(lags, list):
        data[f'Volume lag 1'] = data['Volume'].shift(1) # create lagged volume column
        if market is not None:
            data[f'Market {pred} Lag 1'] = data[f'Market {pred}'].shift(1)
        for lag in lags:
            data[f'{pred} Lag {lag}'] = data[pred].shift(lag) # create lagged price column
    else:
        data[f'{pred} Lag {lags}'] = data[pred].shift(lags)
        data[f'Volume Lag {lags}'] = data['Volume'].shift(lags)
        if market is not None:
            data[f'Market {pred} Lag {lags}'] = data[f'Market {pred}'].shift(lags)
    
    data = data.dropna() # drop missing values

    X = data.drop(['Date', pred, 'Volume'], axis = 1) # training features
    y = pd.DataFrame(data[pred]) # training target
    if market is not None:
        X = X.drop([f'Market {pred}'], axis = 1)

    # scaling
    if scaler == 'minmax':
        X_scaler = MinMaxScaler()
        y_scaler = MinMaxScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())
    
    elif scaler == 'standard':
        X_scaler = StandardScaler()
        y_scaler = StandardScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())

    y = pd.Series(y.values.flatten())

    # train test split
    X_train, X_test = X[:train_size], X[train_size:] # split features into training and testing sets
    y_train, y_test = y[:train_size], y[train_size:] # split target into training and testing sets
    
    # model fitting
    model = Ridge(alpha = penalty) # create Ridge model
    model.fit(X_train, y_train) # fit the model
    train_predictions = model.predict(X_train) # make predictions
    test_predictions = model.predict(X_test) # make predictions
    
    if isinstance(val_metric, list):
        metric = {}
        if scaler is not None:
            y_test_inv = pd.DataFrame(y_test)
            test_predictions_inv = pd.DataFrame(test_predictions)
            y_test_inv = pd.Series(y_scaler.inverse_transform(y_test_inv).flatten())
            test_predictions_inv = pd.Series(y_scaler.inverse_transform(test_predictions_inv).flatten())
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv, pred)
                else:
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv)
        else:
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test, test_predictions, pred)
                else:
                    metric[el] = metric_dict[el](y_test, test_predictions)
        metric = pd.DataFrame(metric.items(), columns = ['Metric', 'Value'])
    
    train_predictions_ret = pd.DataFrame(train_predictions)
    train_predictions_ret = pd.Series(y_scaler.inverse_transform(train_predictions_ret).flatten())
    test_predictions_ret = pd.DataFrame(test_predictions)
    test_predictions_ret = pd.Series(y_scaler.inverse_transform(test_predictions_ret).flatten())
    returns = np.hstack([train_predictions_ret, test_predictions_ret])

    if plot:
        fig = go.Figure()

        # Add the actual values line
        fig.add_trace(go.Scatter(x=data['Date'], y = y, mode='lines', name=f'Actual {pred}', line=dict(color='blue')))

        # Add the predicted values line
        fig.add_trace(go.Scatter(x=data['Date'], y=np.hstack([train_predictions, test_predictions]), mode='lines', name=f'Predicted {pred}', line=dict(color='red')))

        # Update the layout for titles and labels
        fig.update_layout(
            title=f'Predicted vs. Actual {pred}',
            xaxis_title='Date',
            yaxis_title=pred,
            legend_title="Legend",
            showlegend=True)

        # Show the plot
        fig.show()
    
    return model, metric, returns # return results, metric and predictions

In [25]:
# we fit the Ridge model for AAPL stock price
model, metric, returns = ridge_model(aapl_df_price, 'Price', plot=True)
print('The model performances are:\n', metric)

The model performances are:
              Metric       Value
0  Sign Concordance    0.467532
1               MSE  276.004873
2              Roos   -1.299482
3                R2    0.931500


#### Returns - Ridge

In [26]:
model, metric, returns = ridge_model(aapl_df_ret, 'Return', plot=True)
print('The model performances are:\n', metric)

The model performances are:
              Metric     Value
0  Sign Concordance  0.556586
1               MSE  0.000528
2              Roos -0.005894
3                R2 -0.012457


The performance of Ridge regression for the AAPL stock seem to be very similar to that of the OLS model, for both price and return predictions.

### OLS performances for all tickers (and S&P)

#### Price

In [27]:
# create list of the metrics for each stock and combine them into a dataframe
R2s = []
Rooss = []
MSEs = []
for i in range(len(price_dfs) - 1): # iterate over the stock prices dataframes and apply OLS to each stock
    print(f'Fitting model for {stock_tickers[i]}')
    model, metrics, returns = ols_model(price_dfs[i], 'Price', plot=False)
    R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])

ols_price_metrics = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s, 'Roos' : Rooss, 'MSE' : MSEs})
ols_price_metrics

Fitting model for AAPL
Fitting model for BA
Fitting model for T
Fitting model for MGM
Fitting model for AMZN
Fitting model for IBM
Fitting model for TSLA
Fitting model for GOOG


Stock        R2      Roos          MSE
0  AAPL  0.991505 -1.376238    34.229125
1    BA  0.989996 -0.770568    69.331117
2     T  0.966836 -1.295878     0.339202
3   MGM  0.981893 -0.856662     0.576342
4  AMZN  0.986708 -1.178710  1751.306258
5   IBM  0.951813 -1.294733     6.155618
6  TSLA  0.992603 -0.973778   734.314369
7  GOOG  0.969073 -1.443056   579.310813

It seems quite clear that the issue explained in class regarding the R2 is verified in our case. Indeed, the R2 is really high for all the observed stocks, however the out of sample custom R2 (Roos) seems really bad for all the stocks and the MSE is far from good for most of the stocks. Elaborating further on what we could see in the AAPL graph, the predictions are almost always equal to the last observed value, and this probably captures the trend in prices leading to a severe bias in the R2 score.

#### Return

In [28]:
R2s = []
Rooss = []
MSEs = []
Sign_concs = []
for i in range(len(return_dfs) - 1): # iterate over the stock returns dataframes and apply OLS to each stock
    model, metrics, returns = ols_model(return_dfs[i], 'Return', plot=False)
    R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ols_return_metrics = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s, 'Roos' : Rooss, 'MSE' : MSEs, 'Sign Concordance' : Sign_concs})
ols_return_metrics

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.014266 -0.007691  0.000529          0.552876
1    BA -0.005322 -0.005185  0.001487          0.487941
2     T -0.006988 -0.006978  0.000330          0.523191
3   MGM  0.004260  0.004296  0.001763          0.543599
4  AMZN -0.002700  0.000884  0.000456          0.543599
5   IBM -0.007311 -0.007310  0.000405          0.500928
6  TSLA  0.000034  0.006132  0.001915          0.510204
7  GOOG -0.016929 -0.015897  0.000405          0.512059

In this case, there is no significant difference between the R2 and Ross. This may be due to the non-stationarity of the time series, which leads to biased estimates of stock prices. However, for returns, we achieve stationarity since each return is the result of first differencing.

### Ridge performances for all tickers (and S&P) and alpha fine tuning

#### Price

In [29]:
for i in range(len(price_dfs) - 1):
    print('Ridge model performances for', stock_tickers[i], 'with Price as target:\n')
    alphas = np.arange(0.5, 10.5, 0.5)
    MSEs = []
    R2s = []
    Roos = []
    Sign_concordances = []
    for alpha in alphas:
        model, metrics, returns = ridge_model(price_dfs[i], 'Price', penalty = alpha, plot=False)
        MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
        R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
        Roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
        Sign_concordances.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

    print('Best MSE for', stock_tickers[i], 'is', np.min(MSEs), 'with alpha =', alphas[np.argmin(MSEs)])
    print('Best R2 for', stock_tickers[i], 'is', np.max(R2s), 'with alpha =', alphas[np.argmax(R2s)])
    print('Best Roos for', stock_tickers[i], 'is', np.max(Roos), 'with alpha =', alphas[np.argmax(Roos)])
    print('Best Sign Concordance for', stock_tickers[i], 'is', np.max(Sign_concordances), 'with alpha =', alphas[np.argmax(Sign_concordances)])
    print('\n')

Ridge model performances for AAPL with Price as target:

Best MSE for AAPL is 106.50141405563312 with alpha = 0.5
Best R2 for AAPL is 0.9735680912347048 with alpha = 0.5
Best Roos for AAPL is -1.1032646439478015 with alpha = 10.0
Best Sign Concordance for AAPL is 0.48794063079777367 with alpha = 6.5


Ridge model performances for BA with Price as target:

Best MSE for BA is 68.3609039077817 with alpha = 0.5
Best R2 for BA is 0.9901361002721223 with alpha = 0.5
Best Roos for BA is -0.5690244009491461 with alpha = 10.0
Best Sign Concordance for BA is 0.49536178107606677 with alpha = 2.5


Ridge model performances for T with Price as target:

Best MSE for T is 0.3411113632426953 with alpha = 0.5
Best R2 for T is 0.9666488942052197 with alpha = 0.5
Best Roos for T is -0.940430471913386 with alpha = 10.0
Best Sign Concordance for T is 0.48237476808905383 with alpha = 0.5


Ridge model performances for MGM with Price as target:

Best MSE for MGM is 0.5725129821038535 with alpha = 1.0
Best R2

In [30]:
R2s = []
Rooss = []
MSEs = []
Sign_concs = []
for i in range(len(price_dfs) - 1):
    model, metrics, returns = ridge_model(price_dfs[i], 'Price', plot=False, penalty=1)
    R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ridge_price_metrics = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s, 'Roos' : Rooss, 'MSE' : MSEs, 'Sign Concordance' : Sign_concs})
ridge_price_metrics

Stock        R2      Roos          MSE  Sign Concordance
0  AAPL  0.931500 -1.299482   276.004873          0.467532
1    BA  0.989451 -0.743110    73.105742          0.493506
2     T  0.966107 -1.255232     0.346651          0.482375
3   MGM  0.982013 -0.818736     0.572513          0.515770
4  AMZN  0.963042 -1.150914  4869.345886          0.515770
5   IBM  0.947089 -1.237956     6.759072          0.463822
6  TSLA  0.958555 -0.914173  4114.475374          0.484230
7  GOOG  0.959516 -1.426293   758.334785          0.504638

#### Return

In [31]:
for i in range(len(return_dfs) - 1):
    print('Ridge model performances for', stock_tickers[i], 'with Return as target:\n')
    alphas = np.arange(0.5, 10.5, 0.5)
    MSEs = []
    R2s = []
    Roos = []
    Sign_concordances = []
    for alpha in alphas:
        model, metrics, returns = ridge_model(return_dfs[i], 'Return', penalty = alpha, plot=False)
        MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
        R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
        Roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
        Sign_concordances.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

    print('Best MSE for', stock_tickers[i], 'is', np.min(MSEs), 'with alpha =', alphas[np.argmin(MSEs)])
    print('Best R2 for', stock_tickers[i], 'is', np.max(R2s), 'with alpha =', alphas[np.argmax(R2s)])
    print('Best Roos for', stock_tickers[i], 'is', np.max(Roos), 'with alpha =', alphas[np.argmax(Roos)])
    print('Best Sign Concordance for', stock_tickers[i], 'is', np.max(Sign_concordances), 'with alpha =', alphas[np.argmax(Sign_concordances)])
    print('\n')

Ridge model performances for AAPL with Return as target:

Best MSE for AAPL is 0.000524653301393606 with alpha = 10.0
Best R2 for AAPL is -0.006460370691777406 with alpha = 10.0
Best Roos for AAPL is 6.456155895473437e-05 with alpha = 10.0
Best Sign Concordance for AAPL is 0.562152133580705 with alpha = 2.0


Ridge model performances for BA with Return as target:

Best MSE for BA is 0.001483891679451587 with alpha = 10.0
Best R2 for BA is -0.0031206377492067894 with alpha = 10.0
Best Roos for BA is -0.002983635723543765 with alpha = 10.0
Best Sign Concordance for BA is 0.4897959183673469 with alpha = 0.5


Ridge model performances for T with Return as target:

Best MSE for T is 0.0003285727741568224 with alpha = 10.0
Best R2 for T is -0.002935868150379717 with alpha = 10.0
Best Roos for T is -0.002925766217480641 with alpha = 10.0
Best Sign Concordance for T is 0.5213358070500927 with alpha = 0.5


Ridge model performances for MGM with Return as target:

Best MSE for MGM is 0.001764342

In [32]:
R2s = []
Rooss = []
MSEs = []
Sign_concs = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ridge_model(return_dfs[i], 'Return', plot=False, penalty=1)
    R2s.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ridge_return_metrics = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s, 'Roos' : Rooss, 'MSE' : MSEs, 'Sign Concordance' : Sign_concs})
ridge_return_metrics

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.012457 -0.005894  0.000528          0.556586
1    BA -0.005293 -0.005155  0.001487          0.484230
2     T -0.006116 -0.006106  0.000330          0.519481
3   MGM  0.002977  0.003013  0.001765          0.534323
4  AMZN -0.002399  0.001184  0.000455          0.543599
5   IBM -0.006097 -0.006096  0.000404          0.504638
6  TSLA -0.000039  0.006060  0.001915          0.510204
7  GOOG -0.013429 -0.012400  0.000404          0.521336

The results of ridge regression show the same patterns of the OLS ones. AS for the penalty, we decided to try different values and found that there is not a single best performer. For this reason, we opted for an arbitrary penalty of 1.





### Optional 1 - Including the Market in the predictions

In [33]:
R2s_v2 = []
Rooss_v2 = []
MSEs_v2 = []
Sign_concs_v2 = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ols_model(return_dfs[i], 'Return', plot=False, market = sp500_df_ret)
    R2s_v2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss_v2.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs_v2.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs_v2.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ols_return_metrics_v2 = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s_v2, 'Roos' : Rooss_v2, 'MSE' : MSEs_v2, 'Sign Concordance' : Sign_concs_v2})
ols_return_metrics_v2

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.001280  0.005212  0.000522          0.560297
1    BA -0.005944 -0.005806  0.001488          0.484230
2     T -0.003852 -0.003842  0.000329          0.495362
3   MGM -0.023174 -0.023137  0.001812          0.526902
4  AMZN -0.011614 -0.007999  0.000460          0.534323
5   IBM  0.000864  0.000865  0.000401          0.504638
6  TSLA -0.021891 -0.015659  0.001957          0.517625
7  GOOG -0.018540 -0.017506  0.000406          0.513915

In [34]:
R2s_v2 = []
Rooss_v2 = []
MSEs_v2 = []
Sign_concs_v2 = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ridge_model(return_dfs[i], 'Return', plot=False, market = sp500_df_ret, penalty=1)
    R2s_v2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss_v2.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs_v2.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs_v2.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ridge_return_metrics_v2 = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s_v2, 'Roos' : Rooss_v2, 'MSE' : MSEs_v2, 'Sign Concordance' : Sign_concs_v2})
ridge_return_metrics_v2

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.004990  0.001525  0.000524          0.560297
1    BA -0.005861 -0.005724  0.001488          0.486085
2     T -0.004226 -0.004216  0.000329          0.508349
3   MGM -0.013069 -0.013032  0.001794          0.526902
4  AMZN -0.007865 -0.004263  0.000458          0.539889
5   IBM -0.001622 -0.001621  0.000402          0.502783
6  TSLA -0.011552 -0.005383  0.001937          0.521336
7  GOOG -0.016634 -0.015602  0.000405          0.517625

### Optional 2 - Including the Market and 3 lags in the predictions

In [35]:
R2s_v3 = []
Rooss_v3 = []
MSEs_v3 = []
Sign_concs_v3 = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ols_model(return_dfs[i], 'Return', plot=False, market = sp500_df_ret, lags = [1, 2, 3])
    R2s_v3.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss_v3.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs_v3.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs_v3.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ols_return_metrics_v3 = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s_v3, 'Roos' : Rooss_v3, 'MSE' : MSEs_v3, 'Sign Concordance' : Sign_concs_v3})
ols_return_metrics_v3

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.004533  0.002117  0.000525          0.549348
1    BA -0.026639 -0.026510  0.001524          0.471136
2     T -0.023194 -0.023177  0.000336          0.478585
3   MGM -0.038513 -0.038466  0.001845          0.521415
4  AMZN -0.015129 -0.011273  0.000462          0.528864
5   IBM -0.016793 -0.016793  0.000410          0.445065
6  TSLA -0.021782 -0.014949  0.001956          0.521415
7  GOOG -0.021401 -0.020284  0.000408          0.510242

In [36]:
R2s_v3 = []
Rooss_v3 = []
MSEs_v3 = []
Sign_concs_v3 = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ridge_model(return_dfs[i], 'Return', plot=False, market = sp500_df_ret, lags = [1, 2, 3], penalty=0.1)
    R2s_v3.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    Rooss_v3.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    MSEs_v3.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    Sign_concs_v3.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

ridge_return_metrics_v3 = pd.DataFrame({'Stock' : stock_tickers[:-1], 'R2' : R2s_v3, 'Roos' : Rooss_v3, 'MSE' : MSEs_v3, 'Sign Concordance' : Sign_concs_v3})
ridge_return_metrics_v3

Stock        R2      Roos       MSE  Sign Concordance
0  AAPL -0.005161  0.001493  0.000526          0.553073
1    BA -0.025173 -0.025045  0.001522          0.471136
2     T -0.022808 -0.022791  0.000336          0.480447
3   MGM -0.035620 -0.035574  0.001840          0.527002
4  AMZN -0.014468 -0.010614  0.000462          0.527002
5   IBM -0.016805 -0.016805  0.000410          0.448790
6  TSLA -0.020345 -0.013522  0.001954          0.519553
7  GOOG -0.021195 -0.020078  0.000408          0.508380

Results from including the market, if compared to adding both the market and a lag of 3 seem to show that there is not significant difference between these two strategies. It can be said, however, that the inclusion of a 3-period lag leads to a slighlty lower sign concordance.

## Task 3

### Random Forest

In [37]:
def randomforest_model(data, pred, market = None, test_size = 0.25, lags = 1, val_metric = ['Roos', 'MSE', 'R2', 'Sign Concordance'], plot=False, scaler = 'minmax'):
    
    '''we apply the same strategy as in the previous models, but we use a Random Forest model'''
    
    data = data.copy() # make a copy of the data

    if market is not None:
        data[f'Market {pred}'] = market[pred]
    
    train_size = int(len(data) * (1 - test_size)) # calculate training size

    if isinstance(lags, list):
        data[f'Volume lag 1'] = data['Volume'].shift(1) # create lagged volume column
        if market is not None:
            data[f'Market {pred} Lag 1'] = data[f'Market {pred}'].shift(1)
        for lag in lags:
            data[f'{pred} Lag {lag}'] = data[pred].shift(lag) # create lagged price column
    else:
        data[f'{pred} Lag {lags}'] = data[pred].shift(lags)
        data[f'Volume Lag {lags}'] = data['Volume'].shift(lags)
        if market is not None:
            data[f'Market {pred} Lag {lags}'] = data[f'Market {pred}'].shift(lags)
    
    data = data.dropna() # drop missing values

    X = data.drop(['Date', pred, 'Volume'], axis = 1) # training features
    y = pd.DataFrame(data[pred]) # training target
    if market is not None:
        X = X.drop([f'Market {pred}'], axis = 1)

    if scaler == 'minmax':
        X_scaler = MinMaxScaler()
        y_scaler = MinMaxScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())
    
    elif scaler == 'standard':
        X_scaler = StandardScaler()
        y_scaler = StandardScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())

    y = pd.Series(y.values.flatten())

    # train test split
    X_train, X_test = X[:train_size], X[train_size:] # split features into training and testing sets
    y_train, y_test = y[:train_size], y[train_size:] # split target into training and testing sets
    
    # model fitting - random forest
    model = RandomForestRegressor(random_state=42) # create random forest model
    model.fit(X_train, y_train) # fit the model
    train_predictions = model.predict(X_train) # make predictions
    test_predictions = model.predict(X_test) # make predictions

    train_predictions_ret = pd.DataFrame(train_predictions)
    train_predictions_ret = pd.Series(y_scaler.inverse_transform(train_predictions_ret).flatten())
    test_predictions_ret = pd.DataFrame(test_predictions)
    test_predictions_ret = pd.Series(y_scaler.inverse_transform(test_predictions_ret).flatten())
    returns = np.hstack([train_predictions_ret, test_predictions_ret])

    if isinstance(val_metric, list):
        metric = {}
        if scaler is not None:
            y_test_inv = pd.DataFrame(y_test)
            test_predictions_inv = pd.DataFrame(test_predictions)
            y_test_inv = pd.Series(y_scaler.inverse_transform(y_test_inv).flatten())
            test_predictions_inv = pd.Series(y_scaler.inverse_transform(test_predictions_inv).flatten())
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv, pred)
                else:
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv)
        else:
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test, test_predictions, pred)
                else:
                    metric[el] = metric_dict[el](y_test, test_predictions)
        metric = pd.DataFrame(metric.items(), columns = ['Metric', 'Value'])

    if plot:
        fig = go.Figure()

        # Add the actual values line
        fig.add_trace(go.Scatter(x=data['Date'], y = y, mode='lines', name=f'Actual {pred}', line=dict(color='blue')))

        # Add the predicted values line
        fig.add_trace(go.Scatter(x=data['Date'], y=np.hstack([train_predictions, test_predictions]), mode='lines', name=f'Predicted {pred}', line=dict(color='red')))

        # Update the layout for titles and labels
        fig.update_layout(
            title=f'Predicted vs. Actual {pred}',
            xaxis_title='Date',
            yaxis_title=pred,
            legend_title="Legend",
            showlegend=True)

        # Show the plot
        fig.show()

    return model, metric, returns # return results and metric

In [38]:
# we fit the Random Forest model for AAPL stock price
model, metrics, returns = randomforest_model(aapl_df_price, 'Price', plot=True)

Being random forest a tree based method, we believe that the flat area in the test period can be attributed to the trend in the data. Indeed, since values greater than 0.34 are never observed in the training process, the regressor leaves are unable to predict higher values.

In [39]:
# we fit the Random Forest model for AAPL stock return
model, metrics, returns = randomforest_model(aapl_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3, 4, 5], plot=True)

As for the returns, the previous problem does not occur. Furthermore, from the graph it is evident that the Random Forest overfits the training data.

### Neural Network

For the Neural Network, we chose a 3-layered architecture with 32, 16 and 8 neurons for each layer, respectively. Our choice stems from the suggestions in the Gu et al. (2020) paper, where it was noted that optimal performances are reached with shallow networks, with 1-3 layers. 

In [40]:
def nn_model(data, pred, market = None, test_size = 0.25, lags = 1, val_metric = ['Roos', 'MSE', 'R2', 'Sign Concordance'], plot=False, scaler = 'minmax', layers=[32, 16, 8]):
    
    '''we apply the same strategy as in the previous models, but we use a Neural Network model'''
    
    data = data.copy() # make a copy of the data

    if market is not None:
        data[f'Market {pred}'] = market[pred]
    
    train_size = int(len(data) * (1 - test_size)) # calculate training size

    if isinstance(lags, list):
        data[f'Volume lag 1'] = data['Volume'].shift(1) # create lagged volume column
        if market is not None:
            data[f'Market {pred} Lag 1'] = data[f'Market {pred}'].shift(1)
        for lag in lags:
            data[f'{pred} Lag {lag}'] = data[pred].shift(lag) # create lagged price column
    else:
        data[f'{pred} Lag {lags}'] = data[pred].shift(lags)
        data[f'Volume Lag {lags}'] = data['Volume'].shift(lags)
        if market is not None:
            data[f'Market {pred} Lag {lags}'] = data[f'Market {pred}'].shift(lags)
    
    data = data.dropna() # drop missing values

    X = data.drop(['Date', pred, 'Volume'], axis = 1) # training features
    y = pd.DataFrame(data[pred]) # training target
    if market is not None:
        X = X.drop([f'Market {pred}'], axis = 1)

    # scaling
    if scaler == 'minmax':
        X_scaler = MinMaxScaler()
        y_scaler = MinMaxScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())
    
    elif scaler == 'standard':
        X_scaler = StandardScaler()
        y_scaler = StandardScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())

    y = pd.Series(y.values.flatten())

    # train test split
    X_train, X_test = X[:train_size], X[train_size:] # split features into training and testing sets
    y_train, y_test = y[:train_size], y[train_size:] # split target into training and testing sets
    
    # model fitting
    model = Sequential() # create a sequential model
    for layer in layers: # iterate over the layers
        model.add(Dense(layer, activation='relu'))
        # model.add(Dropout(0.2))
    model.add(Dense(1))
    optimizer = Adam(learning_rate=0.01) # set the optimizer
    model.compile(optimizer=optimizer, loss='mean_squared_error')
    callbacks = [EarlyStopping(patience=3, restore_best_weights=True, monitor='val_loss')] # early stopping
    model.fit(X_train, y_train, epochs = 60, batch_size = 32, callbacks=callbacks, validation_split=0.2, verbose=0) # fit the model
    train_predictions = model.predict(X_train) # make predictions
    test_predictions = model.predict(X_test) # make predictions

    train_predictions_ret = pd.DataFrame(train_predictions)
    train_predictions_ret = pd.Series(y_scaler.inverse_transform(train_predictions_ret).flatten())
    test_predictions_ret = pd.DataFrame(test_predictions)
    test_predictions_ret = pd.Series(y_scaler.inverse_transform(test_predictions_ret).flatten())
    returns = np.hstack([train_predictions_ret, test_predictions_ret])
    
    if isinstance(val_metric, list):
        metric = {}
        if scaler is not None:
            y_test_inv = pd.DataFrame(y_test)
            test_predictions_inv = pd.DataFrame(test_predictions)
            y_test_inv = pd.Series(y_scaler.inverse_transform(y_test_inv).flatten())
            test_predictions_inv = pd.Series(y_scaler.inverse_transform(test_predictions_inv).flatten())
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv, pred)
                else:
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv)
        else:
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test, test_predictions, pred)
                else:
                    metric[el] = metric_dict[el](y_test, test_predictions)
        metric = pd.DataFrame(metric.items(), columns = ['Metric', 'Value'])

    if plot:
        fig = go.Figure()

        # Add the actual values line
        fig.add_trace(go.Scatter(x=data['Date'], y = y, mode='lines', name=f'Actual {pred}', line=dict(color='blue')))

        # Add the predicted values line
        fig.add_trace(go.Scatter(x=data['Date'], y=model.predict(X).flatten(), mode='lines', name=f'Predicted {pred}', line=dict(color='red')))

        # Update the layout for titles and labels
        fig.update_layout(
            title=f'Predicted vs. Actual {pred}',
            xaxis_title='Date',
            yaxis_title=pred,
            legend_title="Legend",
            showlegend=True)

        # Show the plot
        fig.show()

    return model, metric, returns # return results and metric

In [41]:
# we fit the Neural Network model for AAPL stock price
model, metrics, returns = nn_model(aapl_df_price, 'Price', plot=True)

51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 487us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 338us/step
68/68 ━━━━━━━━━━━━━━━━━━━━ 0s 225us/step


In [42]:
# we print the metrics for the Neural Network model for AAPL stock return
print(metrics)

             Metric       Value
0  Sign Concordance    0.482375
1               MSE  445.018903
2              Roos   -1.078436
3                R2    0.889554


In [43]:
# we fit the Neural Network model for AAPL stock return
model, metrics, returns = nn_model(aapl_df_ret, 'Return', plot=True)

51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 605us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 664us/step
68/68 ━━━━━━━━━━━━━━━━━━━━ 0s 256us/step


In [44]:
# we print the metrics for the Neural Network model for AAPL stock return
print(metrics)

             Metric     Value
0  Sign Concordance  0.551020
1               MSE  0.000547
2              Roos -0.042403
3                R2 -0.049205


At first glance, it is evident that unlike in the case of a Random Forest, the Neural Network does not overfit the training data, which is in contrast to our expectations. Furthermore, due to the small size of the training data, it is very likely that the network training process does not converge. Therefore, results oscillate despite the presence of a seed. These results must therefore be taken with caution. 

### XGBoost

In [45]:
def xgboost_model(data, pred, market = None, test_size = 0.25, lags = 1, val_metric = ['Roos', 'MSE', 'R2', 'Sign Concordance'], plot=False, scaler = 'minmax', xgb_params = {}):
    
    ''' we apply the same strategy as in the previous models, but we use a XGBoost model'''
    
    data = data.copy() # make a copy of the data

    if market is not None:
        data[f'Market {pred}'] = market[pred]
        data['Market Volume'] = market['Volume']
    
    train_size = int(len(data) * (1 - test_size)) # calculate training size

    if isinstance(lags, list):
        for lag in lags:
            data[f'{pred} Lag {lag}'] = data[pred].shift(lag) # create lagged price column
            data[f'Volume lag {lag}'] = data['Volume'].shift(lag) # create lagged volume column
            if market is not None:
                data[f'Market {pred} Lag {lag}'] = data[f'Market {pred}'].shift(lag)
                data[f'Market Volume Lag {lag}'] = data['Market Volume'].shift(lag)
    else:
        data[f'{pred} Lag {lags}'] = data[pred].shift(lags)
        data[f'Volume Lag {lags}'] = data['Volume'].shift(lags)
        if market is not None:
            data[f'Market {pred} Lag {lags}'] = data[f'Market {pred}'].shift(lags)
            data[f'Market Volume Lag {lags}'] = data['Market Volume'].shift(lags)
    
    data = data.dropna() # drop missing values

    X = data.drop(['Date', pred, 'Volume'], axis = 1) # training features
    y = pd.DataFrame(data[pred]) # training target
    if market is not None:
        X = X.drop([f'Market {pred}', 'Market Volume'], axis = 1)

    # scaling
    if scaler == 'minmax':
        X_scaler = MinMaxScaler()
        y_scaler = MinMaxScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())
    
    elif scaler == 'standard':
        X_scaler = StandardScaler()
        y_scaler = StandardScaler()
        X = X_scaler.fit_transform(X)
        y = pd.Series(y_scaler.fit_transform(y).flatten())

    y = pd.Series(y.values.flatten())

    # train test split
    X_train, X_test = X[:train_size], X[train_size:] # split features into training and testing sets
    y_train, y_test = y[:train_size], y[train_size:] # split target into training and testing sets
    X_train_ft, X_val_ft = X_train[:int(len(X_train) * 0.8)], X_train[int(len(X_train) * 0.8):]
    y_train_ft, y_val_ft =  y_train[:int(len(y_train) * 0.8)], y_train[int(len(y_train) * 0.8):]
    
    # model fitting
    best_model = XGBRegressor() # create XGBoost model
    best_model.fit(X_train_ft, y_train_ft) # fit the model
    best_val_predictions = best_model.predict(X_val_ft) # make predictions
    y_val_inv = pd.DataFrame(y_val_ft)
    val_predictions_inv = pd.DataFrame(best_val_predictions)
    y_val_ft = pd.Series(y_scaler.inverse_transform(y_val_inv).flatten())
    best_val_predictions = pd.Series(y_scaler.inverse_transform(val_predictions_inv).flatten())
    best_roos = roos_metric(y_val_ft, best_val_predictions, pred) # compute the Roos metric for the basic model

    # fine-tuning
    param_grid = {'n_estimators': [100, 200, 300],
                  'max_depth': [3, 4, 5],
                  'learning_rate': [0.01, 0.05, 0.1]}
    for params in tqdm(ParameterGrid(param_grid)): # we perform a grid search over the hyperparameters
        model = XGBRegressor()
        model.set_params(**params)
        model.fit(X_train, y_train)
        train_predictions = model.predict(X_train_ft)
        val_predictions = model.predict(X_val_ft)
        y_val_inv = pd.DataFrame(y_val_ft)
        val_predictions_inv = pd.DataFrame(val_predictions)
        y_val_ft = pd.Series(y_scaler.inverse_transform(y_val_inv).flatten())
        val_predictions = pd.Series(y_scaler.inverse_transform(val_predictions_inv).flatten())
        roos = roos_metric(y_val_ft, val_predictions, pred)
        if roos > best_roos: # we keep the best model
            best_roos = roos
            best_model = model
            best_val_predictions = val_predictions

    best_model.fit(X_train, y_train)
    train_predictions = best_model.predict(X_train)
    test_predictions = best_model.predict(X_test)

    train_predictions_ret = pd.DataFrame(train_predictions)
    train_predictions_ret = pd.Series(y_scaler.inverse_transform(train_predictions_ret).flatten())
    test_predictions_ret = pd.DataFrame(test_predictions)
    test_predictions_ret = pd.Series(y_scaler.inverse_transform(test_predictions_ret).flatten())
    returns = np.hstack([train_predictions_ret, test_predictions_ret])
    
    if isinstance(val_metric, list):
        metric = {}
        if scaler is not None:
            y_test_inv = pd.DataFrame(y_test)
            test_predictions_inv = pd.DataFrame(test_predictions)
            y_test_inv = pd.Series(y_scaler.inverse_transform(y_test_inv).flatten())
            test_predictions_inv = pd.Series(y_scaler.inverse_transform(test_predictions_inv).flatten())
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv, pred)
                else:
                    metric[el] = metric_dict[el](y_test_inv, test_predictions_inv)
        else:
            for el in set(val_metric):
                if el == 'Roos' or el == 'Sign Concordance':
                    metric[el] = metric_dict[el](y_test, test_predictions, pred)
                else:
                    metric[el] = metric_dict[el](y_test, test_predictions)
        metric = pd.DataFrame(metric.items(), columns = ['Metric', 'Value'])

    if plot:
        fig = go.Figure()

        # Add the actual values line
        fig.add_trace(go.Scatter(x=data['Date'], y = y, mode='lines', name=f'Actual {pred}', line=dict(color='blue')))

        # Add the predicted values line
        fig.add_trace(go.Scatter(x=data['Date'], y=np.hstack([train_predictions, test_predictions]), mode='lines', name=f'Predicted {pred}', line=dict(color='red')))

        # Update the layout for titles and labels
        fig.update_layout(
            title=f'Predicted vs. Actual {pred}',
            xaxis_title='Date',
            yaxis_title=pred,
            legend_title="Legend",
            showlegend=True)

        # Show the plot
        fig.show()
    
    return best_model, metric, returns # return results and metric

In [46]:
# we fit the XGBoost model for AAPL stock price
model, metrics, returns = xgboost_model(aapl_df_price, 'Price', plot=True, lags = [1, 2, 3, 4, 5], market = sp500_df_price)
print('The model performances are:\n', metrics)

  0%|          | 0/27 [00:00<?, ?it/s]

The model performances are:
              Metric        Value
0  Sign Concordance     0.484112
1               MSE  6641.403689
2              Roos    -0.372721
3                R2    -0.644946


As in the case of the Random Forest, the model does not predict in the test set values that go beyond the training set's maximum observed value.

In [47]:
# we fit the XGBoost model for AAPL stock return
model, metrics, returns = xgboost_model(aapl_df_ret, 'Return', plot=True, lags = [1, 2, 3, 4, 5], market = sp500_df_ret)
print('The model performances are:\n', metrics)

  0%|          | 0/27 [00:00<?, ?it/s]

The model performances are:
              Metric     Value
0  Sign Concordance  0.502804
1               MSE  0.000536
2              Roos -0.014954
3                R2 -0.021786


Results seem to be in line with those of the Random Forest model.

### Models' performances

In [48]:
# calculate ols metrics for all stocks
ols_roos = []
ols_r2 = []
ols_mse = []
ols_sign_conc = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ols_model(return_dfs[i], 'Return', plot=False)
    ols_roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    ols_r2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    ols_mse.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    ols_sign_conc.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])


# calculate ridge metrics for all stocks
ridge_roos = []
ridge_r2 = []
ridge_mse = []
ridge_sign_conc = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = ridge_model(return_dfs[i], 'Return', plot=False, penalty=1)
    ridge_roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    ridge_r2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    ridge_mse.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    ridge_sign_conc.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

# calculate random forest metrics for all stocks
rf_roos = []
rf_r2 = []
rf_mse = []
rf_sign_conc = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = randomforest_model(return_dfs[i], 'Return', plot=False, market=sp500_df_ret, lags = [1, 2, 3, 4, 5])
    rf_roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    rf_r2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    rf_mse.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    rf_sign_conc.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

# calculate xgboost metrics for all stocks
xgb_roos = []
xgb_r2 = []
xgb_mse = []
xgb_sign_conc = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = xgboost_model(return_dfs[i], 'Return', plot=False, lags = [1, 2, 3, 4, 5], market = sp500_df_ret)
    xgb_roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    xgb_r2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    xgb_mse.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    xgb_sign_conc.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

# calculate neural network metrics for all stocks
nn_roos = []
nn_r2 = []
nn_mse = []
nn_sign_conc = []
for i in range(len(return_dfs) - 1):
    model, metrics, returns = nn_model(return_dfs[i], 'Return', plot=False, market = sp500_df_ret)
    nn_roos.append(metrics[metrics['Metric'] == 'Roos']['Value'].values[0])
    nn_r2.append(metrics[metrics['Metric'] == 'R2']['Value'].values[0])
    nn_mse.append(metrics[metrics['Metric'] == 'MSE']['Value'].values[0])
    nn_sign_conc.append(metrics[metrics['Metric'] == 'Sign Concordance']['Value'].values[0])

# create a dataframe to store the results
ols_scores = pd.DataFrame({'Stock' : stock_tickers[:-1], 'Roos' : ols_roos, 'R2' : ols_r2, 'MSE' : ols_mse, 'Sign Concordance' : ols_sign_conc, 'model' : 'OLS'})
ridge_scores = pd.DataFrame({'Stock' : stock_tickers[:-1], 'Roos' : ridge_roos, 'R2' : ridge_r2, 'MSE' : ridge_mse, 'Sign Concordance' : ridge_sign_conc, 'model' : 'Ridge'})
rf_scores = pd.DataFrame({'Stock' : stock_tickers[:-1], 'Roos' : rf_roos, 'R2' : rf_r2, 'MSE' : rf_mse, 'Sign Concordance' : rf_sign_conc, 'model' : 'Random Forest'})
xgb_scores = pd.DataFrame({'Stock' : stock_tickers[:-1], 'Roos' : xgb_roos, 'R2' : xgb_r2, 'MSE' : xgb_mse, 'Sign Concordance' : xgb_sign_conc, 'model' : 'XGBoost'})
nn_scores = pd.DataFrame({'Stock' : stock_tickers[:-1], 'Roos' : nn_roos, 'R2' : nn_r2, 'MSE' : nn_mse, 'Sign Concordance' : nn_sign_conc, 'model' : 'Neural Network'})

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 502us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 342us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 333us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 511us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 296us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 532us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 333us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 523us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 520us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 527us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 303us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 544us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 300us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 784us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 334us/step


In [49]:
# concatenate all the results
all_scores = pd.concat([ols_scores, ridge_scores, rf_scores, xgb_scores, nn_scores])
avg_scores = all_scores.groupby('model').agg(
    {
        'Roos' : 'mean',
        'R2' : 'mean',
        'MSE' : 'mean',
        'Sign Concordance' : 'mean'
    }
)
avg_scores['model'] = avg_scores.index

In [50]:
# Define colors for each model
model_colors = {
    'Neural Network': '#00CC96',  # Green
    'OLS': '#636EFA',             # Blue
    'Random Forest': '#AB63FA',   # Purple
    'Ridge': '#EF553B',           # Red
    'XGBoost': '#FF6347'          # Tomato
}

# Create subplots
fig = make_subplots(rows=2, cols=2, subplot_titles=('Roos', 'R2', 'MSE', 'Sign Concordance'))

# Create a bar plot for each metric
metrics = ['Roos', 'R2', 'MSE', 'Sign Concordance']
for i, metric in enumerate(metrics):
    row = i // 2 + 1
    col = i % 2 + 1
    
    fig.add_trace(go.Bar(
        x=avg_scores['model'],
        y=avg_scores[metric],
        name=metric,
        marker_color=[model_colors[model] for model in avg_scores['model']]
    ), row=row, col=col)

# Update layout
fig.update_layout(
    title='Model Comparison Across Different Metrics',
    showlegend=False,
    height=800
)

# Show plot
fig.show()

Final results for our model show that linear methods (OLS and Ridge regression) outperform the non-linear methods on all metrics. This is in stark contrast with the results of the Gu et al. paper, where Neural Network and Random Forest models where the best ones. 

Differences between our results and those of the paper are mainly due to the data used for training. Gu et al. did in fact have many more variables that likely had non-linear relationship with the final target. In our case, we simply used the lagged returns and prices for prediction. Moreover the granularity of the data was different: in our analysis, we used daily observations, whose higher noise is likely interpolated by complex models.

In the Jiang et al. paper we have also seen that non-linear models perform better than linear ones. In their case, however, inputs were images, whose patterns may be more easily recognisable than those in time trends. 

## Task 4

In [51]:
# we make a dataset with the true returns for the stocks
true_returns = concat_df_r.iloc[3:,:9].copy()
true_returns.columns = ['Date'] + stock_tickers[:-1]
true_returns

Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19 -0.003169  0.006661  0.002967  0.005499  0.026446 -0.003038   
5    2012-01-20 -0.017417 -0.000529  0.002959 -0.012500 -0.018102  0.044316   
6    2012-01-23  0.016916 -0.000132 -0.003605  0.039557 -0.025350  0.007744   
7    2012-01-24 -0.016378 -0.001987 -0.010197  0.001522  0.004890  0.010264   
8    2012-01-25  0.062439  0.006104  0.003988 -0.003799  0.004278 -0.001042   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05  0.003625  0.055794 -0.005332  0.000000  0.021091 -0.003099   
2155 2020-08-06  0.034889 -0.011935 -0.000335  0.104067  0.006231  0.005341   
2156 2020-08-07 -0.024495 -0.012660  0.006032  0.030878 -0.017842 -0.009198   
2157 2020-08-10  0.014535  0.055229  0.005996  0.137677 -0.006093  0.017206   
2158 2020-08-11 -0.029740  0.004013  0.000000 -0.006928 -0.021438 -0.002832   

          TSLA      GOOG  
4    -0.001865  0.010523  
5    -0.005979 -0.083775  
6     0.006391 -0.000802  
7     0.024281 -0.007839  
8     0.020058 -0.019693  
...        ...       ...  
2154 -0.001332  0.005898  
2155  0.003071  0.017976  
2156 -0.024752 -0.003740  
2157 -0.023501  0.001077  
2158 -0.031144 -0.010547  

[2155 rows x 9 columns]

In [52]:
def investment(data_true, data_pred, budget = 100, n_stocks = 4, fees = 0.00):
    
    '''this function simulates an investment strategy that rebalances 
    the portfolio every day by investing in the n_stocks with the highest predicted returns'''

    a = budget # initial budget
    data_true = data_true.copy()
    data_true.reset_index(drop=True, inplace=True)
    data_pred = data_pred.copy()
    data_pred.reset_index(drop=True, inplace=True)
    for i, row in data_pred.iterrows(): # iterate over the rows of the predictions
        val = row.values[1:] 
        val = np.sort(val)[-n_stocks:] #retrieve the n_stocks with the highest predicted returns
        stocks = row[row.isin(val)].index # retrieve the stock tickers
        stocks = [stock for stock in stocks.values]
        b = 0 # budget goes to zero since we invest all the money again
        for stock in stocks:
            data_true_stock = data_true[stock]
            b += (1 + data_true_stock[i]) * (a / n_stocks) # we rebuild our budget by investing in the stocks with the highest predicted returns
        a = b - (b * fees)

    print('The final budget is:', a)
    return a

#### Using OLS

In [53]:
# apply OLS model to the stock returns and created a dataset with the predictions
aapl_model = ols_model(aapl_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ba_model = ols_model(ba_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
t_model = ols_model(t_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
mgm_model = ols_model(mgm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
amzn_model = ols_model(amzn_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ibm_model = ols_model(ibm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
tsla_model = ols_model(tsla_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
goog_model = ols_model(goog_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]

ols_df_model = pd.DataFrame({'Date' : concat_df_r['Date'][3:], 'AAPL' : aapl_model, 'BA' : ba_model, 'T': t_model, 'MGM' : mgm_model, 'AMZN' : amzn_model, 'IBM' : ibm_model, 'TSLA' : tsla_model, 'GOOG' : goog_model})
ols_df_model

Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19  0.000406  0.000747 -0.000189  0.003161  0.001177  0.000016   
5    2012-01-20 -0.000059  0.001746 -0.000079  0.000230 -0.000487 -0.002432   
6    2012-01-23  0.000104  0.000203  0.000117  0.001735 -0.001012  0.000691   
7    2012-01-24  0.002031  0.000695  0.000467  0.001236  0.001187 -0.000445   
8    2012-01-25  0.000053  0.001352 -0.000204 -0.000801  0.003056  0.001255   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05 -0.001178 -0.000749  0.000563 -0.000380  0.001035 -0.000088   
2155 2020-08-06  0.000049  0.001769 -0.000120  0.001549  0.001840 -0.000750   
2156 2020-08-07  0.002020 -0.002658  0.000658  0.002086  0.000728  0.000590   
2157 2020-08-10 -0.001387  0.000485 -0.000389 -0.002246  0.000651 -0.000714   
2158 2020-08-11  0.001629  0.004010 -0.000270  0.002710  0.001908  0.000918   

          TSLA      GOOG  
4     0.001561  0.000698  
5     0.004227  0.000509  
6     0.001974 -0.002255  
7     0.001925  0.003445  
8     0.001387 -0.000660  
...        ...       ...  
2154  0.002180  0.000448  
2155  0.003726  0.001185  
2156  0.003730  0.001286  
2157  0.002436  0.000607  
2158  0.003082  0.001473  

[2155 rows x 9 columns]

In [54]:
# apply the long portfolio strategy through the OLS model
ols_investment = investment(true_returns.loc[len(ols_df_model) * 0.75:, :], ols_df_model.loc[len(ols_df_model) * 0.75:, :])
ols_investment

The final budget is: 162.84901245068585


162.84901245068585

#### Using Ridge

In [55]:
# apply Ridge model to the stock returns and created a dataset with the predictions
aapl_model = ridge_model(aapl_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
ba_model = ridge_model(ba_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
t_model = ridge_model(t_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
mgm_model = ridge_model(mgm_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
amzn_model = ridge_model(amzn_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
ibm_model = ridge_model(ibm_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
tsla_model = ridge_model(tsla_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]
goog_model = ridge_model(goog_df_ret, 'Return', penalty=1, market = sp500_df_ret, lags = [1, 2, 3])[2]

ridge_df_model = pd.DataFrame({'Date' : concat_df_r['Date'][3:], 'AAPL' : aapl_model, 'BA' : ba_model, 'T': t_model, 'MGM' : mgm_model, 'AMZN' : amzn_model, 'IBM' : ibm_model, 'TSLA' : tsla_model, 'GOOG' : goog_model})
ridge_df_model

Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19  0.000607  0.000938 -0.000055  0.002504  0.001224  0.000207   
5    2012-01-20  0.000167  0.001555 -0.000045  0.000552 -0.000240 -0.002131   
6    2012-01-23  0.000327  0.000434  0.000108  0.001240 -0.000788  0.000080   
7    2012-01-24  0.001755  0.000740  0.000463  0.001283  0.001156 -0.000189   
8    2012-01-25  0.000250  0.001287 -0.000166 -0.000117  0.002919  0.000920   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05 -0.000871 -0.000148  0.000489  0.000188  0.001090 -0.000094   
2155 2020-08-06  0.000242  0.001610  0.000038  0.001310  0.001807 -0.000504   
2156 2020-08-07  0.001787 -0.001224  0.000607  0.002175  0.000768  0.000535   
2157 2020-08-10 -0.000932  0.000464 -0.000371 -0.000824  0.000691 -0.000514   
2158 2020-08-11  0.001481  0.003066 -0.000224  0.002676  0.001831  0.000610   

          TSLA      GOOG  
4     0.001009  0.000833  
5     0.003600  0.000745  
6     0.001965 -0.001494  
7     0.002004  0.002865  
8     0.001707 -0.000370  
...        ...       ...  
2154  0.001955  0.000531  
2155  0.003158  0.001153  
2156  0.003142  0.001218  
2157  0.002107  0.000630  
2158  0.002642  0.001339  

[2155 rows x 9 columns]

In [56]:
# apply the long portfolio strategy through the Ridge model
ridge_investment = investment(true_returns.loc[len(ridge_df_model) * 0.75:, :], ridge_df_model.loc[len(ridge_df_model) * 0.75:, :])
ridge_investment

The final budget is: 168.7146637080155


168.7146637080155

#### Using XGBoost

In [57]:
# apply XGBoost model to the stock returns and created a dataset with the predictions
aapl_model = xgboost_model(aapl_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ba_model = xgboost_model(ba_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
t_model = xgboost_model(t_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
mgm_model = xgboost_model(mgm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
amzn_model = xgboost_model(amzn_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ibm_model = xgboost_model(ibm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
tsla_model = xgboost_model(tsla_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
goog_model = xgboost_model(goog_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]

xgboost_df_model = pd.DataFrame({'Date' : concat_df_r['Date'][3:], 'AAPL' : aapl_model, 'BA' : ba_model, 'T' : t_model, 'MGM' : mgm_model, 'AMZN' : amzn_model, 'IBM' : ibm_model, 'TSLA' : tsla_model, 'GOOG' : goog_model})
xgboost_df_model

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

  0%|          | 0/27 [00:00<?, ?it/s]

Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19  0.002058  0.002080  0.001830  0.003152  0.001568 -0.000955   
5    2012-01-20 -0.004990  0.002572  0.001242 -0.006078 -0.003647  0.028507   
6    2012-01-23 -0.000944  0.001020 -0.002965  0.011042  0.000701  0.006570   
7    2012-01-24 -0.001561  0.000717 -0.002391 -0.002330  0.002504  0.007816   
8    2012-01-25  0.031530  0.000846 -0.000447  0.003820  0.002247 -0.003105   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05  0.000507 -0.000319 -0.000704 -0.001186  0.001177  0.001066   
2155 2020-08-06  0.003235 -0.005318 -0.001698 -0.000988  0.002247  0.002540   
2156 2020-08-07  0.000372  0.002427  0.000244  0.003306  0.001557  0.001205   
2157 2020-08-10  0.001118 -0.003479  0.001214  0.007254  0.002539  0.002174   
2158 2020-08-11  0.004512 -0.003631  0.000294  0.020000  0.002133 -0.002326   

          TSLA      GOOG  
4     0.010845 -0.000178  
5    -0.006005 -0.035062  
6     0.005815 -0.008464  
7     0.002439 -0.006684  
8     0.016970 -0.006564  
...        ...       ...  
2154  0.017898 -0.001725  
2155  0.007980 -0.000484  
2156 -0.000334  0.000758  
2157  0.000851  0.001302  
2158  0.000811 -0.002325  

[2155 rows x 9 columns]

In [58]:
# apply the long portfolio strategy through the XGBoost model
xgboost_investment = investment(true_returns.loc[len(xgboost_df_model) * 0.75:, :], xgboost_df_model.loc[len(xgboost_df_model) * 0.75:, :])
xgboost_investment

The final budget is: 120.1638963252912


120.1638963252912

#### Using Neural Network

In [59]:
# apply Neural Network model to the stock returns and created a dataset with the predictions
aapl_model = nn_model(aapl_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ba_model = nn_model(ba_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
t_model = nn_model(t_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
mgm_model = nn_model(mgm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
amzn_model = nn_model(amzn_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ibm_model = nn_model(ibm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
tsla_model = nn_model(tsla_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
goog_model = nn_model(goog_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]

nn_df_model = pd.DataFrame({'Date' : concat_df_r['Date'][3:], 'AAPL' : aapl_model, 'BA' : ba_model, 'T' : t_model, 'MGM' : mgm_model, 'AMZN' : amzn_model, 'IBM' : ibm_model, 'TSLA' : tsla_model, 'GOOG' : goog_model})
nn_df_model

51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 493us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 361us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 504us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 281us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 491us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 294us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 484us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 290us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 489us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 339us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 1ms/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 514us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 954us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 365us/step
51/51 ━━━━━━━━━━━━━━━━━━━━ 0s 494us/step
17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 321us/step


Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19  0.000528 -0.004100  0.001887  0.006621  0.006991  0.002657   
5    2012-01-20 -0.000091 -0.002051  0.002170  0.005306  0.006904 -0.000292   
6    2012-01-23  0.000092 -0.002987  0.001284  0.003640  0.003142  0.003054   
7    2012-01-24  0.000166 -0.003644 -0.000176  0.003410 -0.001739  0.005583   
8    2012-01-25 -0.000274 -0.004951 -0.000395  0.003879 -0.003569  0.005591   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05  0.000871  0.003740  0.002351  0.001293  0.002291  0.002809   
2155 2020-08-06  0.000095  0.018059  0.000407  0.005674  0.001617  0.002879   
2156 2020-08-07  0.000959  0.010175  0.001662  0.017585  0.003263  0.002585   
2157 2020-08-10 -0.000927 -0.002049  0.001658  0.018244  0.000111  0.000742   
2158 2020-08-11  0.000963  0.006013  0.002056  0.034853 -0.001346  0.001531   

          TSLA      GOOG  
4     0.004179  0.003602  
5     0.006744  0.003743  
6     0.001974  0.000415  
7     0.001475 -0.007990  
8     0.000546 -0.004278  
...        ...       ...  
2154  0.001234 -0.000017  
2155  0.004063  0.001330  
2156  0.002996  0.002903  
2157  0.001695  0.002709  
2158  0.002682  0.001172  

[2155 rows x 9 columns]

In [60]:
# apply the long portfolio strategy through the Neural Network model
nn_investment = investment(true_returns.loc[len(nn_df_model) * 0.75:, :], nn_df_model.loc[len(nn_df_model) * 0.75:, :])
nn_investment

The final budget is: 179.51626962013546


179.51626962013546

#### Using Random Forest

In [61]:
# apply Random Forest model to the stock returns and created a dataset with the predictions
aapl_model = randomforest_model(aapl_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ba_model = randomforest_model(ba_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
t_model = randomforest_model(t_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
mgm_model = randomforest_model(mgm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
amzn_model = randomforest_model(amzn_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
ibm_model = randomforest_model(ibm_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
tsla_model = randomforest_model(tsla_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]
goog_model = randomforest_model(goog_df_ret, 'Return', market = sp500_df_ret, lags = [1, 2, 3])[2]

randomforest_df_model = pd.DataFrame({'Date' : concat_df_r['Date'][3:], 'AAPL' : aapl_model, 'BA' : ba_model, 'T' : t_model, 'MGM' : mgm_model, 'AMZN' : amzn_model, 'IBM' : ibm_model, 'TSLA' : tsla_model, 'GOOG' : goog_model})
randomforest_df_model

Date      AAPL        BA         T       MGM      AMZN       IBM  \
4    2012-01-19 -0.000521  0.003560  0.001549  0.002373  0.017714 -0.001806   
5    2012-01-20 -0.010661  0.002909  0.002076 -0.005535 -0.012414  0.023129   
6    2012-01-23  0.005762 -0.000526 -0.004047  0.022668 -0.011615  0.005764   
7    2012-01-24 -0.009516 -0.001186 -0.005664 -0.001170  0.002614  0.006857   
8    2012-01-25  0.047867  0.005230  0.002162 -0.000876  0.001415 -0.001698   
...         ...       ...       ...       ...       ...       ...       ...   
2154 2020-08-05 -0.001716 -0.001199  0.001859  0.001718 -0.000640  0.001032   
2155 2020-08-06  0.002604  0.001511 -0.001499 -0.003783  0.003201  0.001014   
2156 2020-08-07  0.003621  0.001492  0.003214  0.009017 -0.000891 -0.004987   
2157 2020-08-10 -0.000955 -0.003826 -0.001574  0.014496 -0.000063 -0.000933   
2158 2020-08-11  0.001179  0.021637  0.001634  0.036619 -0.006405 -0.005101   

          TSLA      GOOG  
4    -0.001357  0.007822  
5     0.004107 -0.050753  
6     0.005696 -0.009422  
7     0.016937 -0.010273  
8     0.017180 -0.012592  
...        ...       ...  
2154  0.010213 -0.003163  
2155  0.002121 -0.001250  
2156 -0.007192 -0.000775  
2157 -0.003542  0.002789  
2158  0.014309 -0.003672  

[2155 rows x 9 columns]

In [62]:
# apply the long portfolio strategy through the Random Forest model
randomforest_investment = investment(true_returns.loc[len(randomforest_df_model) * 0.75:, :], randomforest_df_model.loc[len(randomforest_df_model) * 0.75:, :])
randomforest_investment

The final budget is: 149.45238163371334


149.45238163371334

Out of all the methods used, the Neural Network seems to lead to the long portfolio strategy with the highest returns. If we consider an initial budget of a $100, we are able to get to a value of $179.52 at the end of the testing period.

It must be noted that for testing our long portfolio strategy we considered exclusively the same period as that of the test set used for building our models. This is due to the fact that the returns for data in the training set have already been seen by these models during the training process. This would have therefore led to biased estimates, thus resulting in extremely high returns that do not reflect the models' real capabilities. 

### Comparing the results with 1000 random portfolios

In [63]:
def random_portfolios(data_true, n_portfolios = 1000, budget = 100, fees = 0.00):
    np.random.seed(42)
    data_true = data_true.copy()
    data_true = data_true.loc[len(data_true) * 0.75:, :]
    data_true.reset_index(drop=True, inplace=True)
    portfolios = pd.DataFrame()
    for i in range(n_portfolios):
        weights = np.random.random(8)
        weights /= np.sum(weights)
        portfolio = {stock : weights[j] for j, stock in enumerate(data_true.columns[1:])}
        portfolios = pd.concat([portfolios, pd.DataFrame(portfolio, index=[i])], axis=0)

    portfolios['Sum'] = np.nan

    for i, row in portfolios.iterrows():
        portfolios.loc[i, 'Sum'] = np.sum(row.values[:-1])
    
    portfolios['Final Budget'] = np.nan

    for i in range(len(portfolios)):
        a = budget
        for j in range(len(data_true)):
            b = 0
            for stock in data_true.columns[1:]:
                data_true_stock = data_true[stock]
                b += (1 + data_true_stock[j]) * (a * portfolios.loc[i, stock])
            a = b - (b * fees)
        portfolios.loc[i, 'Final Budget'] = a

    return portfolios

In [64]:
portfolios = random_portfolios(true_returns)
portfolios

AAPL        BA         T       MGM      AMZN       IBM      TSLA  \
0    0.096229  0.244263  0.188068  0.153811  0.040085  0.040079  0.014923   
1    0.162039  0.190871  0.005549  0.261453  0.224397  0.057239  0.049013   
2    0.102714  0.177161  0.145828  0.098321  0.206566  0.047094  0.098630   
3    0.135249  0.232846  0.059214  0.152497  0.175682  0.013775  0.180169   
4    0.015077  0.219922  0.223804  0.187362  0.070600  0.022637  0.158584   
..        ...       ...       ...       ...       ...       ...       ...   
995  0.322144  0.115435  0.047276  0.171709  0.219302  0.011352  0.100760   
996  0.089957  0.191563  0.210300  0.136336  0.034593  0.193863  0.110484   
997  0.207622  0.170623  0.164819  0.159745  0.045127  0.047530  0.155040   
998  0.088230  0.157284  0.157677  0.091165  0.159333  0.168672  0.131695   
999  0.103144  0.118514  0.043968  0.102824  0.078868  0.171396  0.341957   

         GOOG  Sum  Final Budget  
0    0.222543  1.0    104.223020  
1    0.049439  1.0    127.198331  
2    0.123686  1.0    137.597388  
3    0.050569  1.0    149.751478  
4    0.102014  1.0    122.416215  
..        ...  ...           ...  
995  0.012022  1.0    167.616330  
996  0.032904  1.0    116.885769  
997  0.049493  1.0    144.638239  
998  0.045943  1.0    135.980659  
999  0.039329  1.0    184.792619  

[1000 rows x 10 columns]

In [65]:
# Extract the returns of the random portfolios
random_portfolio_returns = portfolios['Final Budget']

# Create the histogram
fig = go.Figure()

# Add the histogram for random portfolios
fig.add_trace(go.Histogram(
    x=random_portfolio_returns,
    name='Random Portfolios',
    marker_color='blue',
    opacity=0.75,
    nbinsx=120
))

# Add a column for OLS
fig.add_trace(go.Histogram(
    x=[ols_investment],
    name='Optimal Portfolio (OLS)',
    marker_color='black',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for OLS
fig.add_shape(
    type="line",
    x0=ols_investment,
    y0=0,
    x1=ols_investment,
    y1=50,
    line=dict(color="black", width=2, dash="dash"),
    name='Optimal Portfolio (OLS)'
)

# Add a column for ridge
fig.add_trace(go.Histogram(
    x=[ridge_investment],
    name='Optimal Portfolio (Ridge)',
    marker_color='red',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for ridge
fig.add_shape(
    type="line",
    x0=ridge_investment,
    y0=0,
    x1=ridge_investment,
    y1=50,
    line=dict(color="red", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Add a column for XGBoost
fig.add_trace(go.Histogram(
    x=[xgboost_investment],
    name='Optimal Portfolio (XGBoost)',
    marker_color='green',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for XGBoost
fig.add_shape(
    type="line",
    x0=xgboost_investment,
    y0=0,
    x1=xgboost_investment,
    y1=50,
    line=dict(color="green", width=2, dash="dash"),
    name='Optimal Portfolio (XGBoost)'
)

# Add a column for neural network
fig.add_trace(go.Histogram(
    x=[nn_investment],
    name='Optimal Portfolio (NN)',
    marker_color='orange',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for neural network
fig.add_shape(
    type="line",
    x0=nn_investment,
    y0=0,
    x1=nn_investment,
    y1=50,
    line=dict(color="orange", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Add a column for random forest
fig.add_trace(go.Histogram(
    x=[randomforest_investment],
    name='Optimal Portfolio (Random Forest)',
    marker_color='purple',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for random forest
fig.add_shape(
    type="line",
    x0=randomforest_investment,
    y0=0,
    x1=randomforest_investment,
    y1=50,
    line=dict(color="purple", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Update the layout for titles and labels
fig.update_layout(
    title='Histogram of Portfolio Final Budgets',
    xaxis_title='Final Budget',
    yaxis_title='Number of Portfolios',
    legend_title='Legend',
    showlegend=True
)

# Show the plot
fig.show()

In the previous plot we can finally compare the performances of our daily re-balanced portfolios (using different models) to that of 1000 portfolios with random weights assigned. We can observe that the two tree-based models perform the words. In second and third place we can then find Ridge and OLS, respectively. Finally, it is confirmed that the best performing portfolio seems to be the Neural Network one. 

As for the random portfolios, the greatest majority of them has a worse performance than out top 3 models. Despite some outliers, which perform even better than the Neural Network one, AI-based portfolios generally perform better. 

### Introducing fees

In [66]:
# add a fee of 3% to the OLS portfolio
ols_investment_fee = investment(true_returns.loc[len(ols_df_model) * 0.75:, :], ols_df_model.loc[len(ols_df_model) * 0.75:, :], fees=0.03)
ols_investment_fee

The final budget is: 1.1017044447436955e-05


1.1017044447436955e-05

In [67]:
# add a fee of 3% to the Ridge portfolio
ridge_investment_fee = investment(true_returns.loc[len(ridge_df_model) * 0.75:, :], ridge_df_model.loc[len(ridge_df_model) * 0.75:, :], fees=0.03)
ridge_investment_fee

The final budget is: 1.1413866876033083e-05


1.1413866876033083e-05

In [68]:
# add a fee of 3% to the XGBoost portfolio
xgboost_investment_fee = investment(true_returns.loc[len(xgboost_df_model) * 0.75:, :], xgboost_df_model.loc[len(xgboost_df_model) * 0.75:, :], fees=0.03)
xgboost_investment_fee

The final budget is: 8.129315412298415e-06


8.129315412298415e-06

In [69]:
# add a fee of 3% to the Neural Network portfolio
nn_investment_fee = investment(true_returns.loc[len(nn_df_model) * 0.75:, :], nn_df_model.loc[len(nn_df_model) * 0.75:, :], fees=0.03)
nn_investment_fee

The final budget is: 1.2144615995396346e-05


1.2144615995396346e-05

In [70]:
# add a fee of 3% to the Random Forest portfolio
randomforest_investment_fee = investment(true_returns.loc[len(randomforest_df_model) * 0.75:, :], randomforest_df_model.loc[len(randomforest_df_model) * 0.75:, :], fees=0.03)
randomforest_investment_fee

The final budget is: 1.0110736973198003e-05


1.0110736973198003e-05

All investment strategies lead to a budget that is very close to 0 at the end of our testing period. This is due to the fact that the daily fee of 3% is higher than the portfolios' daily returns.

Just to try - is it in line with the random portfolios?

In [71]:
fee_portfolios = random_portfolios(true_returns, fees = 0.03)
fee_portfolios

AAPL        BA         T       MGM      AMZN       IBM      TSLA  \
0    0.096229  0.244263  0.188068  0.153811  0.040085  0.040079  0.014923   
1    0.162039  0.190871  0.005549  0.261453  0.224397  0.057239  0.049013   
2    0.102714  0.177161  0.145828  0.098321  0.206566  0.047094  0.098630   
3    0.135249  0.232846  0.059214  0.152497  0.175682  0.013775  0.180169   
4    0.015077  0.219922  0.223804  0.187362  0.070600  0.022637  0.158584   
..        ...       ...       ...       ...       ...       ...       ...   
995  0.322144  0.115435  0.047276  0.171709  0.219302  0.011352  0.100760   
996  0.089957  0.191563  0.210300  0.136336  0.034593  0.193863  0.110484   
997  0.207622  0.170623  0.164819  0.159745  0.045127  0.047530  0.155040   
998  0.088230  0.157284  0.157677  0.091165  0.159333  0.168672  0.131695   
999  0.103144  0.118514  0.043968  0.102824  0.078868  0.171396  0.341957   

         GOOG  Sum  Final Budget  
0    0.222543  1.0      0.000007  
1    0.049439  1.0      0.000009  
2    0.123686  1.0      0.000009  
3    0.050569  1.0      0.000010  
4    0.102014  1.0      0.000008  
..        ...  ...           ...  
995  0.012022  1.0      0.000011  
996  0.032904  1.0      0.000008  
997  0.049493  1.0      0.000010  
998  0.045943  1.0      0.000009  
999  0.039329  1.0      0.000013  

[1000 rows x 10 columns]

In [72]:
# Extract the returns of the random portfolios
fee_random_portfolio_returns = fee_portfolios['Final Budget']

# Create the histogram
fig = go.Figure()

# Add the histogram for random portfolios
fig.add_trace(go.Histogram(
    x=fee_random_portfolio_returns,
    name='Random Portfolios',
    marker_color='blue',
    opacity=0.75,
    nbinsx=120
))

# Add a column for OLS
fig.add_trace(go.Histogram(
    x=[ols_investment_fee],
    name='Optimal Portfolio (OLS)',
    marker_color='black',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for OLS
fig.add_shape(
    type="line",
    x0=ols_investment_fee,
    y0=0,
    x1=ols_investment_fee,
    y1=50,
    line=dict(color="black", width=2, dash="dash"),
    name='Optimal Portfolio (OLS)'
)


# Add a column for ridge
fig.add_trace(go.Histogram(
    x=[ridge_investment_fee],
    name='Optimal Portfolio (Ridge)',
    marker_color='red',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for ridge
fig.add_shape(
    type="line",
    x0=ridge_investment_fee,
    y0=0,
    x1=ridge_investment_fee,
    y1=50,
    line=dict(color="red", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Add a column for XGBoost
fig.add_trace(go.Histogram(
    x=[xgboost_investment_fee],
    name='Optimal Portfolio (XGBoost)',
    marker_color='green',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for XGBoost
fig.add_shape(
    type="line",
    x0=xgboost_investment_fee,
    y0=0,
    x1=xgboost_investment_fee,
    y1=50,
    line=dict(color="green", width=2, dash="dash"),
    name='Optimal Portfolio (XGBoost)'
)

# Add a column for neural network
fig.add_trace(go.Histogram(
    x=[nn_investment_fee],
    name='Optimal Portfolio (NN)',
    marker_color='orange',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for neural network
fig.add_shape(
    type="line",
    x0=nn_investment_fee,
    y0=0,
    x1=nn_investment_fee,
    y1=50,
    line=dict(color="orange", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Add a column for random forest
fig.add_trace(go.Histogram(
    x=[randomforest_investment_fee],
    name='Optimal Portfolio (Random Forest)',
    marker_color='purple',
    opacity=0.75,
    nbinsx=1
))
# Add a vertical line for random forest
fig.add_shape(
    type="line",
    x0=randomforest_investment_fee,
    y0=0,
    x1=randomforest_investment_fee,
    y1=50,
    line=dict(color="purple", width=2, dash="dash"),
    name='Optimal Portfolio (Ridge)'
)

# Update the layout for titles and labels
fig.update_layout(
    title='Histogram of Portfolio Final Budgets',
    xaxis_title='Final Budget',
    yaxis_title='Number of Portfolios',
    legend_title='Legend',
    showlegend=True
)

# Show the plot
fig.show()

Results are identical to those of the previous section. In this case, however, the final budget is almost null, in all the simulated, as well as the AI-generated, porfolios.